# Sokoban, search & classical planning

Aleksander Sadikov, 2023

This notebook demonstrates the principles (and power) of classical AI planning. 

Our domain will be the well-known computer game Sokoban. For the rules and some interesting facts, see https://en.wikipedia.org/wiki/Sokoban.

*Domain description.* In planning, the domain is described with relations that are true/false at any given time. Remember, only things important for solving the problem are worth describing. The relations in this domain are thus: (1) the position of Mr Soko-ban ('m', (r,c)), (2) the positions of boxes ('b', (r,c), and (3) whether a square is clear ('c', (r,c)). As you can see, all relations are given as tuples, the (r,c) part is a coordinate (r=row, c=column).

*Actions.* The actions, or moves in search terminology, are described in STRIPS style, i.e. in terms of preconditions (when the action can take place) and effects (what the action does). The latter are divided into two parts, namely what the action establishes (adds) in the world and what it destroys (deletes). Both preconditions and effects are expressed in terms of the relations that are either true or false in the current world (domain). 

The planning method used in this notebook is goal regression planning. 

In [1]:
# imports
from copy import deepcopy
import numpy as np

## Sokoban as a planning problem

In [15]:
# this is the planning domain description class
# it uses goal regression planning
# (as opposed to the search version below)
class pSokoban:
    def __init__(self, world=None):
        if world:
            # world description given 
            self.world = deepcopy(world[0])
            self.goals = world[1]
        else:
            # default world (set it up)
            # 0 is empty square, 1 is wall, 2 is Soko-ban, 3 is box
            self.world = np.array([[1,1,1,1],
                                   [1,0,1,1],
                                   [1,3,2,1],
                                   [1,0,0,1],
                                   [1,1,1,1]])
            self.goals = [(1,1)]
        self.Setup()

    def Setup(self):
        # define starting goals, i.e. final positions of all boxes
        self.state_goals = set()
        for coors in self.goals: self.state_goals.add( ('b', coors) )
        
        # express the given world as a set of relations being true in it for easy "solved" check
        self.state_start = set()
        maxr, maxc = self.world.shape
        for r in range(maxr):
            for c in range(maxc):
                if self.world[r,c] == 2: self.state_start.add(('m',(r,c)))
                if self.world[r,c] == 3: self.state_start.add(('b',(r,c)))
                if self.world[r,c] == 0: self.state_start.add(('c',(r,c)))
        # and store the number of boxes in this world for quicker consistency check
        # no move should "spawn" new boxes
        self.nboxes = len([t for t, _ in self.state_start if t == 'b'])
        
        # no move history yet
        self.history = []
        
    def Solved(self):
        # simply check if the current goals are a subset of the starting world position
        # note that <= is a subset operator if arguments are sets
        return self.state_goals <= self.state_start

    def CheckConsistency(self, move):
        # check if all the current goals are consistent with one another 
        # after making a given move
        # these are the move limitations due to domain knowledge
        c = True
        self.Move(move)
        # two things cannot be at the same location (including clears)
        # check if set of all coordinates (set makes them unique)
        # has less elemenents than the number of all goals
        if len(set([(r,c) for _, (r,c) in self.state_goals])) < len(self.state_goals):
            c = False
        # Mr Soko-ban cannot be at two locations
        if c and len([t for t, _ in self.state_goals if t == 'm']) > 1:
            c = False
        # new boxes cannot be spawned or "stacked into each other" by the move
        if c and len([t for t, _ in self.state_goals if t == 'b']) != self.nboxes:
            c = False
        self.UndoMove(move)
        return c
    
    def SortGoals(self):
        # sort goals so those not true at START are prioritised
        # this is a domain independent heuristic that can speed up the search
        # but it can also be hurtful
        #   e.g. when it has to destroy something already achieved at START
        priority, rest = [], []
        for t, coors in self.state_goals:
            if t == 'm':
                if self.world[coors] == 2: rest.append((t, coors))
                else: priority.append((t, coors))
            if t == 'b':
                if self.world[coors] == 3: rest.append((t, coors))
                else: priority.append((t, coors))
            if t == 'c':
                if self.world[coors] == 0: rest.append((t, coors))
                else: priority.append((t, coors))
        return priority + rest
    
    def GenerateMoves(self):
        # domain knowledge: walls are static; we can use this to detect impossible pushes
        cands = []  # candidate moves
        maxr, maxc = self.world.shape  # for out-of-bounds checks
        # sort the goals before generating moves (a speed-up domain-independent heuristic)
        sorted_goals = self.SortGoals()
        for t, (r,c) in sorted_goals:
            # goal is to get box into (r,c); only pushes can echieve that
            if t == 'b':
                if r+2<maxr and self.world[r+2,c] != 1:  # approach box from below, no wall there
                    cands.append(('pU',(r,c)))
                if r-2>=0 and self.world[r-2,c] != 1:  # approach box from above, no wall there
                    cands.append(('pD',(r,c)))
                if c+2<maxc and self.world[r,c+2] != 1:  # approach box from right, no wall there
                    cands.append(('pL',(r,c)))
                if c-2>=0 and self.world[r,c-2] != 1:  # approach box from left, no wall there
                    cands.append(('pR',(r,c)))
            # goal is to get Soko-ban into (r,c); both pushes and moves can do it
            if t == 'm':
                # pushes should be from (r,c) into adjacent cells
                # perhaps additional wall checks are possible (needed?)
                if self.world[r+1,c] != 1 and self.world[r-1,c] != 1:  
                    # approach box from below, no wall there; also no wall where box is pushed to
                    cands.append(('pU',(r-1,c)))
                if self.world[r-1,c] != 1 and self.world[r+1,c] != 1:  
                    # approach box from above, no wall there; also no wall where box is pushed to
                    cands.append(('pD',(r+1,c)))
                if self.world[r,c+1] != 1 and self.world[r,c-1] != 1:  
                    # approach box from right, no wall there; also no wall where box is pushed to
                    cands.append(('pL',(r,c-1)))
                if self.world[r,c-1] != 1 and self.world[r,c+1] != 1:  
                    # approach box from left, no wall there; also no wall where box is pushed to
                    cands.append(('pR',(r,c+1)))
                # moves are into (r,c)
                if self.world[r+1,c] != 1:  # come from below, no wall there
                    cands.append(('U',(r,c)))
                if self.world[r-1,c] != 1:  # come from above, no wall there
                    cands.append(('D',(r,c)))
                if self.world[r,c+1] != 1:  # come from right, no wall there
                    cands.append(('L',(r,c)))
                if self.world[r,c-1] != 1:  # come from left, no wall there
                    cands.append(('R',(r,c)))
            # goal is to clear location (r,c); both pushes and moves can do it
            if t == 'c':
                # it is *always* Mr Soko-ban at (r,c), but he can either move or push out
                # into an adjacent cell
                # if box is at (r,c) then Mr Soko-ban gets into that cell by pushing
                # and this doesn't clear the cell
                if self.world[r-1,c] != 1:  # moving up, no wall should be there
                    cands.append(('U',(r-1,c)))
                if self.world[r+1,c] != 1:  # moving down, no wall should be there
                    cands.append(('D',(r+1,c)))
                if self.world[r,c-1] != 1:  # moving left, no wall should be there
                    cands.append(('L',(r,c-1)))
                if self.world[r,c+1] != 1:  # moving right, no wall should be there
                    cands.append(('R',(r,c+1)))
                # pushes of boxes in *adjacent* cells
                if r-2>=0 and self.world[r-2,c] != 1:  # up
                    cands.append(('pU',(r-2,c)))
                if r+2<maxr and self.world[r+2,c] != 1:  # down
                    cands.append(('pD',(r+2,c)))
                if c-2>=0 and self.world[r,c-2] != 1:  # left
                    cands.append(('pL',(r,c-2)))
                if c+2<maxc and self.world[r,c+2] != 1:  # right
                    cands.append(('pR',(r,c+2)))
        # check consistency of all candidate moves and only keep the consistent ones
        moves = []
        for move in cands:
            if move not in moves and self.CheckConsistency(move): moves.append(move)
        return moves
        
    def Move(self, move):
        # make a move using the regression formula
        
        # first prepare the adds(A) and preconditions cans(A) 
        # for given action A (here denoted as move)
        t, (r,c) = move
        if t == 'pU':
            # push box up into pos (r,c); Soko-ban is then at (r+1,c) and (r+2,c) becomes clear
            adds = {('b', (r  ,c)), ('m', (r+1,c)), ('c', (r+2,c))}
            cans = {('b', (r+1,c)), ('m', (r+2,c)), ('c', (r  ,c))}
        if t == 'pD':
            # push box down into pos (r,c); Soko-ban is then at (r-1,c) and (r-2,c) becomes clear
            adds = {('b', (r  ,c)), ('m', (r-1,c)), ('c', (r-2,c))}
            cans = {('b', (r-1,c)), ('m', (r-2,c)), ('c', (r  ,c))}
        if t == 'pL':
            # push box left into pos (r,c); Soko-ban is then at (r,c+1) and (r,c+2) becomes clear
            adds = {('b', (r  ,c)), ('m', (r,c+1)), ('c', (r,c+2))}
            cans = {('b', (r,c+1)), ('m', (r,c+2)), ('c', (r  ,c))}
        if t == 'pR':
            # push box right into pos (r,c); Soko-ban is then at (r,c-1) and (r,c-2) becomes clear
            adds = {('b', (r  ,c)), ('m', (r,c-1)), ('c', (r,c-2))}
            cans = {('b', (r,c-1)), ('m', (r,c-2)), ('c', (r  ,c))}
        if t == 'U':
            # move Mr Soko-ban up into pos (r,c); cell (r+1,c) becomes clear
            adds = {('m', (r  ,c)), ('c', (r+1,c))}
            cans = {('m', (r+1,c)), ('c', (r  ,c))}
        # move Mr Soko-ban down into pos (r,c)
        if t == 'D':
            # move Mr Soko-ban down into pos (r,c); cell (r-1,c) becomes clear
            adds = {('m', (r  ,c)), ('c', (r-1,c))}
            cans = {('m', (r-1,c)), ('c', (r  ,c))}
        # move Mr Soko-ban left into pos (r,c)
        if t == 'L':
            # move Mr Soko-ban left into pos (r,c); cell (r,c+1) becomes clear
            adds = {('m', (r  ,c)), ('c', (r,c+1))}
            cans = {('m', (r,c+1)), ('c', (r  ,c))}
        if t == 'R':
            # move Mr Soko-ban right into pos (r,c); cell (r,c-1) becomes clear
            adds = {('m', (r  ,c)), ('c', (r,c-1))}
            cans = {('m', (r,c-1)), ('c', (r  ,c))}
            
        # save current state for potential undo
        self.history.append(self.state_goals)        

        # use regression formula to make a move: RG = (G - adds(A)) ∪ cans(A)
        self.state_goals = (self.state_goals - adds) | cans
        
    def UndoMove(self, move):
        # simply pull up the last saved state from history
        self.state_goals = self.history.pop()

    def ExecuteSequence(self, sequence):
        for m in sequence:
            self.Move(m)

    def UndoSequence(self, sequence):
        for m in reversed(sequence):
            self.UndoMove(m)
    
    def PrintPosition(self):
        chars = ['   ', '###', ' S ', ' ⌧']
        height, width = self.world.shape
        print('   ', end='')
        for c in range(width):
            print('%2d ' % c, end='')
        print()
        for r in range(height):
            print('%2d ' % r, end='')
            for c in range(width):
                if self.world[(r,c)] == 0 and (r,c) in self.goals: 
                    print(' o ', end='')  # goal square (printed only if not occupied)
                    #print(' · ', end='')  # goal square (printed only if not occupied)
                    continue
                print(chars[self.world[(r,c)]], end='')
            print()

### First steps

In [16]:
# let's start with the predefined world
# which is already contained in the pSokoban class
s = pSokoban()

In [17]:
s.PrintPosition()

    0  1  2  3 
 0 ############
 1 ### o ######
 2 ### ⌧ S ###
 3 ###      ###
 4 ############


This is the world (problem) that we used in class this year (actually Mr Soko-ban was in square (3,2) in class version). We used it to demonstrate what actions would goal regression consider when solving this problem. Remember, goal regression starts from the solved position and works its way back until the set of current goals it needs to satisfy (achieve) are are subset of the starting position.

Let's see this in practice.

In [18]:
# this is/are the initial goal(s)
s.state_goals

{('b', (1, 1))}

Makes sense, the only box in the world needs to be pushed into square (1,1). Let's next see which actions goal regression considers to achieve this.

In [19]:
s.GenerateMoves()

[('pU', (1, 1))]

Right, 'pU' means "push box UP into (1,1)". And yes, the planner understands that this is the only option as square (1,1) cannot be accessed in any other way. Let's make this move (action) and see what happens next.

In [20]:
s.Move(('pU', (1, 1)))

In [21]:
# what the goals are after the move above
s.state_goals

{('b', (2, 1)), ('c', (1, 1)), ('m', (3, 1))}

Ok, now we have three goals. The box needs to appear at (2,1) so it can next be pushed into (1,1), which should be clear. And Mr Soko-ban needs to be at (3,1) to do the push. Of course, the preconditions for the move ('pU', (1,1) were added to the goals. At the same time, the effect of that move the planner found useful was achieved by the move and removed from the goals -- ('b', (1,1)).

And which moves will the planner consider doing now?

In [22]:
s.GenerateMoves()

[('L', (3, 1))]

Again, only one possibility. We've seen that in class. The other options, while achieving some of the goals, are not possible due to domain limitations. Thus, they are considered, but removed (the CheckConsistency method is primarily responsible for that). Ok, let's do this move.

In [23]:
s.Move(('L', (3, 1)))

In [24]:
s.state_goals

{('b', (2, 1)), ('c', (1, 1)), ('c', (3, 1)), ('m', (3, 2))}

Let's see if the problem is already solved. Remember, in class this year, Mr Soko-ban was in square (3,2) and the problem was solved in two steps. Not the case here, though, we need one more step at least.

In [25]:
s.Solved()

False

No, the problem is not solved yet. Which actions goal regression planner considers next?

In [26]:
s.GenerateMoves()

[('D', (3, 2)), ('R', (3, 2))]

Now, two actions are considered. The second one we know is bad, but the planner would/could try it, and you can do it here as well for practice or if curious. In this notebook I'll go with the first one, leading to the solution immediately.

In [27]:
s.Move(('D', (3, 2)))

In [28]:
s.Solved()

True

We got to the solution manually. Later in the notebook, we'll leave the work to the planner -- actually to the search employed (or guided) by the planner.

### Setting up custom problems

Now, let's see how we can define our own problem and give it to the planner. In this way you can create your own little problems to try out. However, note that Python is not all that fast and without macro moves or other heuristics only relatively small problems can be solved in reasonable time.

In [29]:
# level 0 position
w0 = np.array([[1,1,1,1,1,1],
               [1,0,0,1,1,1],
               [1,0,0,1,1,1],
               [1,0,2,0,0,1],
               [1,0,0,3,0,1],
               [1,0,0,1,1,1],
               [1,1,1,1,1,1]])
g0 = ((1,2),)   # the goals are a tuple (even if there is only one goal hence the final comma)
lvl0 = (w0,g0)  # the problem is described as a tuple (world, goals)

The position/problem is composed of two parts. First, the description of the world (w0 above). It is given as a numpy array where *1s* represent a wall, *2* is Mr Soko-ban, *3s* represent boxes, and *0s* mean empty (currently clear) squares. Please note that the wall *must* be all around the world as the implementation depends on it for some checks (it's easier/faster this way). Second, a tuple of goals (g0) gives (row,column) coordinates of final positions of the boxes. Note that in Sokoban it doesn't matter which box is in which final position as long as they all are in final positions.

This is how you set this position up.

In [30]:
s = pSokoban(lvl0)

In [31]:
s.PrintPosition()

    0  1  2  3  4  5 
 0 ##################
 1 ###    o #########
 2 ###      #########
 3 ###    S       ###
 4 ###       ⌧   ###
 5 ###      #########
 6 ##################


### Solving problems automatically

The problem above requires 13 steps if solved optimally. This is too long to track manually, of course. And besides, we want to see real planning in action. Let's do that.

In [32]:
import bsearch

Wait a minute. This is the library with basic search methods we've used previously. Well, yes, of course it is, because... huh, because goal regression planning is using search! One can think of it as the planner guiding the search in the sense it only considers actions which are somehow relevant (and not any legal/possible action). Relevant here means that at least one of the current goals (state_goals variable) is immediately achieved by the considered action (is in the action's *adds* list).

Let's first use the knowledge that the optimal solution is 13 moves (actions) long and therefore use depth-first search for this first demonstration.

In [59]:
solution = bsearch.DF(s, 13)  # depth-first search with depth limit of 13

In [60]:
len(solution)

13

In [36]:
# to more easily check the solution below
s.PrintPosition()

    0  1  2  3  4  5 
 0 ##################
 1 ###    o #########
 2 ###      #########
 3 ###    S       ###
 4 ###       ⌧   ###
 5 ###      #########
 6 ##################


In [34]:
solution

[('pU', (1, 2)),
 ('pU', (2, 2)),
 ('pU', (3, 2)),
 ('R', (5, 2)),
 ('D', (5, 1)),
 ('D', (4, 1)),
 ('L', (3, 1)),
 ('L', (3, 2)),
 ('U', (3, 3)),
 ('pL', (4, 2)),
 ('D', (4, 4)),
 ('R', (3, 4)),
 ('R', (3, 3))]

Note that the solution is given *backwards*! Goal regression works from the goal towards the start, remember. So, we go right twice, then down, the push the box left (pL), and so on... Check it, but it seems correct.

## Sokoban as a pure search problem

Sokoban can, of course, be defined also as a pure search problem. We do this below very much in the same fashion as we defined the GridWorld problem in one of the earlier notebooks. We will use this to compare the planning and search versions.

In [48]:
# this is the pure search version of the Sokoban world description
# pSokoban class above = planning, sSokoban (this) = pure search
class sSokoban:
    def __init__(self, world=None):
        if world:
            # world description given 
            self.world = deepcopy(world[0])
            p = np.nonzero(self.world == 2)    # get position of the chararter (Mr Soko-ban)
            self.pos = (p[0][0], p[1][0])
            self.goals = world[1]
        else:
            # default world (set it up)
            # 0 is empty square, 1 is wall, 2 is Soko-ban, 3 is box
            self.world = np.array([[1,1,1,1,1,1],
                                   [1,0,0,1,1,1],
                                   [1,0,0,1,1,1],
                                   [1,0,2,0,0,1],
                                   [1,0,0,3,0,1],
                                   [1,0,0,1,1,1],
                                   [1,1,1,1,1,1]])
            self.pos = (3,2)
            self.goals = [(1,2)]
    
    def Solved(self):
        s = True
        p = np.nonzero(self.world == 3)  # get positions of boxes
        for coors in zip(*p):
            if coors not in self.goals:
                s = False
                break
        return s
    
    def GenerateMoves(self):
        # moves could simply be left, right, up, and down (and pushes implicit)
        # but for nicer output, pushes are separated (also makes Move/UndoMove a bit easier)
        # having the wall (represented as ones) all around the world serves as a guard
        # and makes it easier as no additional out-of-bounds checks are needed
        moves = []
        r, c = self.pos  # for easier access
        if self.world[r,c-1] == 0: moves.append('L')  # go left
        if self.world[r,c-1] == 3 and self.world[r,c-2] == 0: moves.append('pL')  # push left
        if self.world[r,c+1] == 0: moves.append('R')  # go right
        if self.world[r,c+1] == 3 and self.world[r,c+2] == 0: moves.append('pR')  # push right
        if self.world[r-1,c] == 0: moves.append('U')  # go up
        if self.world[r-1,c] == 3 and self.world[r-2,c] == 0: moves.append('pU')  # push up
        if self.world[r+1,c] == 0: moves.append('D')  # go down
        if self.world[r+1,c] == 3 and self.world[r+2,c] == 0: moves.append('pD')  # push down
        return moves
    
    def Move(self, move):
        r, c = self.pos
        self.world[r,c] = 0
        if move == 'L':            # go left
            self.world[r,c-1] = 2
            self.pos = (r,c-1)
        if move == 'pL':           # push left
            self.world[r,c-1] = 2
            self.world[r,c-2] = 3
            self.pos = (r,c-1)
        if move == 'R':            # go right
            self.world[r,c+1] = 2
            self.pos = (r,c+1)
        if move == 'pR':           # push right
            self.world[r,c+1] = 2
            self.world[r,c+2] = 3
            self.pos = (r,c+1)
        if move == 'U':            # go up
            self.world[r-1,c] = 2
            self.pos = (r-1,c)
        if move == 'pU':           # push up
            self.world[r-1,c] = 2
            self.world[r-2,c] = 3
            self.pos = (r-1,c)
        if move == 'D':            # go down
            self.world[r+1,c] = 2
            self.pos = (r+1,c)
        if move == 'pD':           # push down
            self.world[r+1,c] = 2
            self.world[r+2,c] = 3
            self.pos = (r+1,c)

    def UndoMove(self, move):
        r, c = self.pos
        if move == 'L':            # reverse go left
            self.world[r,c] = 0
            self.world[r,c+1] = 2
            self.pos = (r,c+1)
        if move == 'pL':           # reverse push left
            self.world[r,c+1] = 2
            self.world[r,c] = 3
            self.world[r,c-1] = 0
            self.pos = (r,c+1)
        if move == 'R':            # reverse go right
            self.world[r,c] = 0
            self.world[r,c-1] = 2
            self.pos = (r,c-1)
        if move == 'pR':           # reverse push right
            self.world[r,c-1] = 2
            self.world[r,c] = 3
            self.world[r,c+1] = 0
            self.pos = (r,c-1)
        if move == 'U':            # reverse go up
            self.world[r,c] = 0
            self.world[r+1,c] = 2
            self.pos = (r+1,c)
        if move == 'pU':           # reverse push up
            self.world[r+1,c] = 2
            self.world[r,c] = 3
            self.world[r-1,c] = 0
            self.pos = (r+1,c)
        if move == 'D':            # reverse go down
            self.world[r,c] = 0
            self.world[r-1,c] = 2
            self.pos = (r-1,c)
        if move == 'pD':           # reverse push down
            self.world[r-1,c] = 2
            self.world[r,c] = 3
            self.world[r+1,c] = 0
            self.pos = (r-1,c)
            
    def ExecuteSequence(self, sequence):
        for m in sequence:
            self.Move(m)

    def UndoSequence(self, sequence):
        for m in reversed(sequence):
            self.UndoMove(m)
    
    def PrintPosition(self):
        chars = ['   ', '###', ' S ', ' ⌧']
        height, width = self.world.shape
        print('   ', end='')
        for c in range(width):
            print('%2d ' % c, end='')
        print()
        for r in range(height):
            print('%2d ' % r, end='')
            for c in range(width):
                if self.world[(r,c)] == 0 and (r,c) in self.goals: 
                    print(' o ', end='')  # goal square (printed only if not occupied)
                    #print(' · ', end='')  # goal square (printed only if not occupied)
                    continue
                print(chars[self.world[(r,c)]], end='')
            print()

### Setting up custom problems and solving them using search

This is done pretty much in the same way as with the planning version before. We will set up the lvl0 problem defined above. No change is needed as both versions (planning, search) accept the same format.

In [49]:
s2 = sSokoban(lvl0)

In [56]:
s2.PrintPosition()

    0  1  2  3  4  5 
 0 ##################
 1 ###    o #########
 2 ###      #########
 3 ###    S       ###
 4 ###       ⌧   ###
 5 ###      #########
 6 ##################


In [52]:
s2.GenerateMoves()

['L', 'R', 'U', 'D']

In [53]:
s2.Move('D')

In [54]:
s2.GenerateMoves()

['L', 'pR', 'U', 'D']

In [55]:
s2.UndoMove('D')

All set up and checked. The move generator for the search version simply moves Mr Soko-ban in any direction, the box movement is almost a consequence of it (although denoted with a 'p').

## Comparing both versions: planning vs pure search

Ok, it's time to see which version performs better. And by better we mean faster. Note that *s* is our planning version and *s2* is the pure search version of the problem.

In [57]:
import cProfile

In [58]:
cProfile.run('solDF2 = bsearch.DF(s2, 13)')

         20540531 function calls (17640654 primitive calls) in 22.553 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
   993444    0.462    0.000    2.463    0.000 <__array_function__ internals>:2(nonzero)
   993444    2.077    0.000    4.540    0.000 <ipython-input-48-a0a6993e2d91>:24(Solved)
   993443    6.025    0.000    6.237    0.000 <ipython-input-48-a0a6993e2d91>:33(GenerateMoves)
  2899877    3.982    0.000    3.982    0.000 <ipython-input-48-a0a6993e2d91>:50(Move)
  2899877    3.962    0.000    3.962    0.000 <ipython-input-48-a0a6993e2d91>:82(UndoMove)
        1    0.000    0.000   22.553   22.553 <string>:1(<module>)
2899878/1    3.832    0.000   22.553   22.553 bsearch.py:10(DF)
   993444    0.103    0.000    0.103    0.000 fromnumeric.py:1800(_nonzero_dispatcher)
   993444    0.293    0.000    1.501    0.000 fromnumeric.py:1804(nonzero)
   993444    0.394    0.000    1.208    0.000 fromnumeric.py:55(_wrapfunc)


Ok, search expands almost exactly 1M nodes (993,444). Let's see how goal regression planning does.

In [61]:
cProfile.run('solDF = bsearch.DF(s, 13)')

         461112 function calls (458088 primitive calls) in 0.366 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
    43119    0.090    0.000    0.093    0.000 <ipython-input-15-1e4220863340>:155(Move)
    43119    0.020    0.000    0.024    0.000 <ipython-input-15-1e4220863340>:202(UndoMove)
     1158    0.001    0.000    0.001    0.000 <ipython-input-15-1e4220863340>:41(Solved)
    40095    0.096    0.000    0.276    0.000 <ipython-input-15-1e4220863340>:46(CheckConsistency)
    40095    0.038    0.000    0.038    0.000 <ipython-input-15-1e4220863340>:55(<listcomp>)
    27364    0.021    0.000    0.021    0.000 <ipython-input-15-1e4220863340>:58(<listcomp>)
     5432    0.004    0.000    0.004    0.000 <ipython-input-15-1e4220863340>:61(<listcomp>)
     1157    0.008    0.000    0.009    0.000 <ipython-input-15-1e4220863340>:66(SortGoals)
     1157    0.063    0.000    0.352    0.000 <ipython-input-15-1e4220863340>:84(Gene

Wow! It's almost instant and expands only 1,158 nodes. But we should note expanding these nodes takes much more time due to all the checks planning does, so the time for expansion is generally not the same...

What about other types of search? After all, breadth-first would be the algorithm of choice since we (usually) don't know the optimal depth limit. However, it might run out of space, so let's use iterative deepening as the safer choice.

In [62]:
cProfile.run('solID2 = bsearch.ID(s2)')

         45877237 function calls (39409895 primitive calls) in 50.435 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
  2223092    1.019    0.000    5.535    0.000 <__array_function__ internals>:2(nonzero)
  2223092    4.687    0.000   10.222    0.000 <ipython-input-48-a0a6993e2d91>:24(Solved)
  2223091   13.429    0.000   13.899    0.000 <ipython-input-48-a0a6993e2d91>:33(GenerateMoves)
  6467342    8.890    0.000    8.890    0.000 <ipython-input-48-a0a6993e2d91>:50(Move)
  6467342    8.815    0.000    8.815    0.000 <ipython-input-48-a0a6993e2d91>:82(UndoMove)
        1    0.000    0.000   50.435   50.435 <string>:1(<module>)
6467356/14    8.609    0.000   50.435    3.602 bsearch.py:10(DF)
        1    0.000    0.000   50.435   50.435 bsearch.py:23(ID)
  2223092    0.233    0.000    0.233    0.000 fromnumeric.py:1800(_nonzero_dispatcher)
  2223092    0.654    0.000    3.390    0.000 fromnumeric.py:1804(nonzero)
  2223092 

In [63]:
cProfile.run('solID = bsearch.ID(s)')

         146081400 function calls (144906336 primitive calls) in 112.691 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
 13603586   27.972    0.000   28.967    0.000 <ipython-input-15-1e4220863340>:155(Move)
 13603586    6.369    0.000    7.655    0.000 <ipython-input-15-1e4220863340>:202(UndoMove)
   409988    0.165    0.000    0.165    0.000 <ipython-input-15-1e4220863340>:41(Solved)
 12428522   30.149    0.000   83.954    0.000 <ipython-input-15-1e4220863340>:46(CheckConsistency)
 12428522   10.727    0.000   10.727    0.000 <ipython-input-15-1e4220863340>:55(<listcomp>)
  8754710    5.974    0.000    5.974    0.000 <ipython-input-15-1e4220863340>:58(<listcomp>)
  2198773    1.392    0.000    1.392    0.000 <ipython-input-15-1e4220863340>:61(<listcomp>)
   409987    2.586    0.000    2.817    0.000 <ipython-input-15-1e4220863340>:66(SortGoals)
   409987   19.574    0.000  107.268    0.000 <ipython-input-15-1e4220863340>

Interesting! Pure search takes less time, but expands 2.2M nodes compared to just over 400k for planning. But note that planning with DF before expanded only 1.1k nodes. The levels without the solution (all before depth 13) really hurt it as it had to check all the possibilities...

So, it's not completely clear who wins...

Planning with breadth-first would probably be safe as it should generate much less nodes as we can see from above. Well, even pure search should fit in memory. Let's see.

In [64]:
cProfile.run('solBF2 = bsearch.BF23(s2)')

         62891898 function calls in 85.333 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
  1458017    0.845    0.000    4.431    0.000 <__array_function__ internals>:2(nonzero)
  1458017    4.655    0.000   28.832    0.000 <ipython-input-48-a0a6993e2d91>:121(ExecuteSequence)
  1458017    5.089    0.000   29.721    0.000 <ipython-input-48-a0a6993e2d91>:125(UndoSequence)
  1458017    5.940    0.000   10.372    0.000 <ipython-input-48-a0a6993e2d91>:24(Solved)
  1458016    9.593    0.000    9.984    0.000 <ipython-input-48-a0a6993e2d91>:33(GenerateMoves)
 17724573   24.176    0.000   24.176    0.000 <ipython-input-48-a0a6993e2d91>:50(Move)
 17724573   24.632    0.000   24.632    0.000 <ipython-input-48-a0a6993e2d91>:82(UndoMove)
        1    0.145    0.145   85.333   85.333 <string>:1(<module>)
        1    0.676    0.676   85.188   85.188 bsearch.py:62(BF23)
  1458017    5.087    0.000   84.512    0.000 bsearch.py:71(auxBF23

In [65]:
cProfile.run('solBF = bsearch.BF23(s)')

         105761990 function calls in 94.504 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
 11161983   26.009    0.000   27.141    0.000 <ipython-input-15-1e4220863340>:155(Move)
 11161983    5.812    0.000    7.347    0.000 <ipython-input-15-1e4220863340>:202(UndoMove)
   263557    1.259    0.000    7.758    0.000 <ipython-input-15-1e4220863340>:206(ExecuteSequence)
   263557    0.911    0.000    3.041    0.000 <ipython-input-15-1e4220863340>:210(UndoSequence)
   263557    0.143    0.000    0.143    0.000 <ipython-input-15-1e4220863340>:41(Solved)
  8144572   22.659    0.000   64.033    0.000 <ipython-input-15-1e4220863340>:46(CheckConsistency)
  8144572    8.368    0.000    8.368    0.000 <ipython-input-15-1e4220863340>:55(<listcomp>)
  5734862    4.458    0.000    4.458    0.000 <ipython-input-15-1e4220863340>:58(<listcomp>)
  1449461    1.045    0.000    1.045    0.000 <ipython-input-15-1e4220863340>:61(<listcomp>)
   

Timewise quite similar (on my tablet at least) with huge advantage in expanded nodes for the planning version. But it's unclear nevertheless. Let's try some other problems.

### More than one box

In [66]:
# level with two boxes and not so simple solution 
# (12 moves, has to move one box from its goal position to clear access to move the other box)
w4 = np.array([[1,1,1,1,1,1],
               [1,0,0,2,0,1],
               [1,0,0,0,0,1],
               [1,0,3,3,0,1],
               [1,0,0,0,0,1],
               [1,0,1,1,0,1],
               [1,1,1,1,1,1]])
g4 = ((3,2), (3,4))
lvl4 = (w4,g4)

Let's go with breadth-first search for both versions. Try others at home if you wish.

In [68]:
s = pSokoban(lvl4)
s2 = sSokoban(lvl4)

In [69]:
s.PrintPosition()

    0  1  2  3  4  5 
 0 ##################
 1 ###       S    ###
 2 ###            ###
 3 ###    ⌧ ⌧ o ###
 4 ###            ###
 5 ###   ######   ###
 6 ##################


Note than one goal square is hidden as the box is already there (3,2). But it will have to be moved...

In [70]:
# planning
cProfile.run('solBF = bsearch.BF23(s)')

         51175713 function calls in 45.565 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
  5332513   12.459    0.000   12.966    0.000 <ipython-input-15-1e4220863340>:155(Move)
  5332513    2.756    0.000    3.441    0.000 <ipython-input-15-1e4220863340>:202(UndoMove)
   103347    0.489    0.000    3.018    0.000 <ipython-input-15-1e4220863340>:206(ExecuteSequence)
   103347    0.346    0.000    1.187    0.000 <ipython-input-15-1e4220863340>:210(UndoSequence)
   103347    0.057    0.000    0.057    0.000 <ipython-input-15-1e4220863340>:41(Solved)
  4169010   11.308    0.000   32.658    0.000 <ipython-input-15-1e4220863340>:46(CheckConsistency)
  4169010    4.673    0.000    4.673    0.000 <ipython-input-15-1e4220863340>:55(<listcomp>)
  2718573    2.378    0.000    2.378    0.000 <ipython-input-15-1e4220863340>:58(<listcomp>)
   531858    0.445    0.000    0.445    0.000 <ipython-input-15-1e4220863340>:61(<listcomp>)
   1

In [71]:
solBF

[('pD', (3, 2)),
 ('L', (1, 2)),
 ('U', (1, 3)),
 ('U', (2, 3)),
 ('pR', (3, 4)),
 ('pU', (2, 2)),
 ('L', (4, 2)),
 ('L', (4, 3)),
 ('D', (4, 4)),
 ('D', (3, 4)),
 ('D', (2, 4)),
 ('R', (1, 4))]

In [73]:
len(solBF)

12

In [72]:
# pure search
cProfile.run('solBF2 = bsearch.BF23(s2)')

         14575167 function calls in 19.317 seconds

   Ordered by: standard name

   ncalls  tottime  percall  cumtime  percall filename:lineno(function)
   359950    0.196    0.000    1.025    0.000 <__array_function__ internals>:2(nonzero)
   359950    0.994    0.000    6.180    0.000 <ipython-input-48-a0a6993e2d91>:121(ExecuteSequence)
   359950    1.077    0.000    6.396    0.000 <ipython-input-48-a0a6993e2d91>:125(UndoSequence)
   359950    1.734    0.000    2.759    0.000 <ipython-input-48-a0a6993e2d91>:24(Solved)
   359949    2.382    0.000    2.477    0.000 <ipython-input-48-a0a6993e2d91>:33(GenerateMoves)
  3845871    5.186    0.000    5.186    0.000 <ipython-input-48-a0a6993e2d91>:50(Move)
  3845871    5.318    0.000    5.318    0.000 <ipython-input-48-a0a6993e2d91>:82(UndoMove)
        1    0.038    0.038   19.317   19.317 <string>:1(<module>)
        1    0.158    0.158   19.279   19.279 bsearch.py:62(BF23)
   359950    1.181    0.000   19.120    0.000 bsearch.py:71(auxBF23

So, more than one box is not a problem for neither version (as it shouldn't be). And the discrepancy remains, less expanded nodes with planning, but faster execution with pure search. No verdict!

Below I give some additional problems to experiment with. Feel free to modify them and to try them out. I'm also still running some much harder problems to see what happens with them as I suspect DF (with known depth limit) might solve some really tough problems, but only with the planning version. But this is a hypothesis at this stage. I promise to tell you what happens...

### Description of some more Sokoban problems

In [175]:
# level 1 position
# too difficult for now
w1 = np.array([[1,1,1,1,1,1],
               [1,0,0,1,1,1],
               [1,0,0,1,1,1],
               [1,3,2,0,0,1],
               [1,0,0,3,0,1],
               [1,0,0,1,1,1],
               [1,1,1,1,1,1]])
g1 = ((1,2), (3,1))
lvl1 = (w1,g1)

In [176]:
# level with two boxes and a super simple solution
w2 = np.array([[1,1,1,1,1,1],
               [1,0,0,0,1,1],
               [1,3,0,3,1,1],
               [1,0,2,0,1,1],
               [1,0,0,0,0,1],
               [1,1,0,0,0,1],
               [1,1,1,1,1,1]])
g2 = ((1,1), (1,3))
lvl2 = (w2,g2)

In [177]:
# level with two boxes and a tad less simple solution
w3 = np.array([[1,1,1,1,1,1],
               [1,0,0,0,0,1],
               [1,3,0,3,0,1],
               [1,0,2,0,0,1],
               [1,0,0,0,0,1],
               [1,1,0,0,0,1],
               [1,1,1,1,1,1]])
g3 = ((1,1), (1,4))
lvl3 = (w3,g3)

In [178]:
# level with two boxes and not so simple solution 
# (12 moves, has to move one box from its goal position to clear access to move the other box)
w4 = np.array([[1,1,1,1,1,1],
               [1,0,0,2,0,1],
               [1,0,0,0,0,1],
               [1,0,3,3,0,1],
               [1,0,0,0,0,1],
               [1,0,1,1,0,1],
               [1,1,1,1,1,1]])
g4 = ((3,2), (3,4))
lvl4 = (w4,g4)

In [179]:
# level nine (solution length 27 or shortened to 24 by slightly changing one goal position)
w9 = np.array([[1,1,1,1,1,1],
               [1,0,0,2,1,1],
               [1,0,3,3,0,1],
               [1,1,0,0,0,1],
               [1,1,1,0,0,1],
               [1,1,1,1,0,1],
               [1,1,1,1,1,1]])
g9  = ((1,1), (5,4))
g9a = ((1,2), (5,4))
lvl9 = (w9,g9)
lvl9a = (w9,g9a)  # solution length shortened to 24

In [185]:
# level 0 position of lengths 13-16
w0 = np.array([[1,1,1,1,1,1],
               [1,2,0,1,1,1],
               [1,0,0,1,1,1],
               [1,0,0,0,0,1],
               [1,0,0,3,0,1],
               [1,0,0,1,1,1],
               [1,1,1,1,1,1]])
g0 = ((1,2),)
lvl0 = (w0,g0)

In [189]:
# level 0+ position of lengths 17-18
w0 = np.array([[1,1,1,1,1,1,1],
               [1,2,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,0,0,0,1],
               [1,0,0,0,3,0,1],
               [1,0,0,1,1,1,1],
               [1,1,1,1,1,1,1]])
g0 = ((1,2),)
lvl0 = (w0,g0)

In [193]:
# level 0+ position of lengths 19-20
w0 = np.array([[1,1,1,1,1,1,1],
               [1,2,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,0,0,0,1],
               [1,0,0,0,3,0,1],
               [1,0,0,1,1,1,1],
               [1,1,1,1,1,1,1]])
g0 = ((1,2),)
lvl0 = (w0,g0)

In [47]:
# level 0+ position of lengths 21-22
w0 = np.array([[1,1,1,1,1,1,1],
               [1,2,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,0,0,0,1],
               [1,0,0,0,3,0,1],
               [1,0,0,1,1,1,1],
               [1,1,1,1,1,1,1]])
g0 = ((1,2),)
lvl0 = (w0,g0)

In [56]:
# level 0+ position of lengths 23-24
w0 = np.array([[1,1,1,1,1,1,1],
               [1,2,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,1,1,1,1],
               [1,0,0,0,0,0,1],
               [1,0,0,0,3,0,1],
               [1,0,0,1,1,1,1],
               [1,1,1,1,1,1,1]])
g0 = ((1,2),)
lvl0 = (w0,g0)

In [194]:
s20 = pSokoban(lvl0)

In [195]:
s20.PrintPosition()

    0  1  2  3  4  5  6 
 0 #####################
 1 ### S  o ############
 2 ###      ############
 3 ###      ############
 4 ###               ###
 5 ###          ⌧   ###
 6 ###      ############
 7 #####################


In [197]:
sol20

[('pU', (1, 2)),
 ('pU', (2, 2)),
 ('pU', (3, 2)),
 ('pU', (4, 2)),
 ('R', (6, 2)),
 ('D', (6, 1)),
 ('D', (5, 1)),
 ('L', (4, 1)),
 ('L', (4, 2)),
 ('U', (4, 3)),
 ('pL', (5, 2)),
 ('pL', (5, 3)),
 ('D', (5, 5)),
 ('R', (4, 5)),
 ('R', (4, 4)),
 ('R', (4, 3)),
 ('D', (4, 2)),
 ('D', (3, 2)),
 ('D', (2, 2)),
 ('R', (1, 2))]